## References

[RAG](https://python.langchain.com/docs/expression_language/cookbook/retrieval)  

[runnanbles - API](https://api.python.langchain.com/en/latest/core_api_reference.html#module-langchain_core.runnables)  
[RunnableParallel](https://python.langchain.com/docs/expression_language/how_to/map)  
[RunnablePassthrough](https://python.langchain.com/docs/expression_language/how_to/passthrough)  

[memory - API](https://api.python.langchain.com/en/latest/langchain_api_reference.html#module-langchain.memory)  
[Chat with history](https://python.langchain.com/docs/use_cases/question_answering/chat_history)  
[]()  
[]()  


In [2]:
import os
import gradio as gr

from operator import itemgetter

# Langchain
from langchain.chains import RetrievalQA
from langchain.prompts import ChatPromptTemplate, MessagesPlaceholder, PromptTemplate
from langchain_core.runnables import RunnableParallel,RunnablePassthrough,RunnableLambda
from langchain_core.output_parsers import StrOutputParser
from langchain_core.messages import AIMessage, HumanMessage, get_buffer_string
from langchain.schema import format_document

# Conversation memory
from langchain.memory.buffer_window import ConversationBufferWindowMemory
from langchain.memory import ConversationBufferMemory


# HuggingFace
from langchain_community.embeddings import HuggingFaceEmbeddings

# GeminiPro
from langchain_google_genai import ChatGoogleGenerativeAI

# Groq
from langchain_groq import ChatGroq

# Pinecone vector database
from pinecone import Pinecone, ServerlessSpec
from langchain_pinecone import PineconeVectorStore


Select an LLM model

In [3]:
# ChatGPT
# model = ChatOpenAI(temperature=0.0)

# Gemini
# model = ChatGoogleGenerativeAI(
#     model="gemini-pro", temperature=0.1, convert_system_message_to_human=True
# )

# Groq
# llama2-70b-4096 (4k), mixtral-8x7b-32768 (32k)
model = ChatGroq(model_name='mixtral-8x7b-32768')


Embeddings and vector store

In [5]:

setid = "global"

embeddings = HuggingFaceEmbeddings(model_name=os.getenv("EMBEDDINGS_MODEL"))
    
pc = Pinecone( api_key=os.getenv("PINECONE_API_KEY") )
index = pc.Index(setid)
vectorstore = PineconeVectorStore(index, embeddings, "text")
retriever = vectorstore.as_retriever(kwargs={"k":5})            # Find 5 documents


Prompts

In [6]:
template_no_history = """Answer the question based only on the following context:
{context}

Question: {question}
"""
PROMPT_NH = ChatPromptTemplate.from_template(template_no_history)

template_with_history = """Given the following conversation history, answer the follow up question:
Chat History:
{chat_history}

Question: {question}
"""
PROMPT_WH = ChatPromptTemplate.from_template(template_with_history)


In [7]:
question = "What is a blockchain?"

# chain = (
#     pipeLog 
#     | { "context": vectorstore.as_retriever(kwargs={"k":5}), "question": RunnablePassthrough() }
#     | PROMPT_NH 
#     | pipeLog 
#     | model
# )


chain = (
    { "context": vectorstore.as_retriever(kwargs={"k": 5}), "question": RunnablePassthrough() }
    | PROMPT_NH
    | model
)


response = chain.invoke(question)
print(response)


content='Based on the provided document, a blockchain is a type of distributed ledger technology that implements a decentralized, fully replicated append-only ledger in a peer-to-peer network. It consists of a chain of blocks, where each block contains a list of validated and timestamped transactions. Blockchain technology is known for its secure and immutable record-keeping of digital transactions, as well as its resistance to tampering and censorship due to its decentralized nature. In a blockchain network, multiple participants, or nodes, maintain copies of the ledger, and processing and verifying transactions are the responsibility of every node. Blockchain technology can be classified as public, private/permissioned, or hybrid.' response_metadata={'token_usage': {'completion_time': 0.269, 'completion_tokens': 151, 'prompt_time': 1.5510000000000002, 'prompt_tokens': 1712, 'queue_time': None, 'total_time': 1.8200000000000003, 'total_tokens': 1863}, 'model_name': 'mixtral-8x7b-32768'

In [8]:
history = [ 
    ["Que es blockchain?", "Blockchain es una cadena de bloques"],
    ["Para que se usa", "Para registrar transacciones"]
]

chat_history = ""
for l in history:
    chat_history += " : ".join(l)
    chat_history += "\n"

chat_history

'Que es blockchain? : Blockchain es una cadena de bloques\nPara que se usa : Para registrar transacciones\n'

In [9]:
chain = (
    { "chat_history": itemgetter('chat_history'), "question": itemgetter('question') }
    | PROMPT_WH 
    | model
)
response = chain.invoke({ "chat_history": chat_history, "question": "Que es consenso?"})
response


AIMessage(content='En la tecnología de blockchain, "consenso" se refiere al mecanismo por el cual se llega a un acuerdo sobre el estado del registro distribuido. Hay varios algoritmos de consenso, como Proof of Work (PoW) y Proof of Stake (PoS), que se utilizan para asegurar la exactitud y la validez de las transacciones en la red blockchain. El algoritmo de consenso ayuda a evitar la duplicación de entradas y garantiza que las transacciones sean seguras y verificables.\n\nEn resumen, consenso en blockchain es el proceso de llegar a un acuerdo sobre el estado del registro distribuido, usando algoritmos para asegurar la exactitud y validez de las transacciones.', response_metadata={'token_usage': {'completion_time': 0.355, 'completion_tokens': 195, 'prompt_time': 0.063, 'prompt_tokens': 68, 'queue_time': None, 'total_time': 0.418, 'total_tokens': 263}, 'model_name': 'mixtral-8x7b-32768', 'system_fingerprint': 'fp_1cc6d039b0', 'finish_reason': 'stop', 'logprobs': None})

## Using parallel runnable jobs

In [10]:
def format_docs(docs):
    return "\n\n".join(doc.page_content for doc in docs)

rag_chain_from_docs = (
    RunnablePassthrough.assign(context=(lambda x: format_docs(x["context"])))
    | PROMPT_NH
    | model
    | StrOutputParser()
)

rag_chain_with_source = RunnableParallel(
    {"context": retriever, "question": RunnablePassthrough()}
).assign(answer=rag_chain_from_docs)


In [11]:
response = rag_chain_with_source.invoke("What is a blockchain?")
response


{'context': [Document(page_content='2\n\nBackground\n\n2.1\n\nBlockchain technology\n\nThe blockchain technology implements a decentralized fully replicated append-only ledger in a\npeer-to-peer network, originally employed for the Bitcoin cryptocurrency [7]. All participating\nnodes maintain a full local copy of the blockchain. The blockchain consists of a sequence\nof blocks containing the transactions of the ledger. Transactions inside blocks are sorted\nchronologically and each block contains a cryptographic hash of the previous block in the\nchain. Nodes create new blocks as they receives transactions, which are broadcast in the\nnetwork. Once a block is complete, they start the consensus process to convince other nodes\nto include it in the blockchain. In the original blockchain technology employed in Bitcoin\nthe consensus process is based on Proof-of-Work (PoW) [7]. With PoW nodes compete with\neach other in confirming transactions and creating new blocks by solving a mathemati

In [12]:
response['question'], response['answer']

('What is a blockchain?',
 'A blockchain is a decentralized fully replicated append-only ledger in a peer-to-peer network, consisting of a chain of blocks containing transactions of the ledger. Each block contains a cryptographic hash of the previous block in the chain, creating an immutable and secure ledger of transactions. The structure enables trust and transparency in the network by allowing participants to verify and validate transactions without the need for intermediaries. It comprises components such as nodes, transactions, and blocks. Nodes maintain a full local copy of the blockchain and are responsible for processing and verifying transactions. Transactions are the smallest and most fundamental part of the blockchain, while blocks are linked to the previous one through cryptographic hashes. The procedures for block validation are depicted by the block version number given to each block in the blockchain. A timestamp value indicates when the particular block was created.')

In [13]:
for doc in response['context']:
    print( doc.metadata['source'] )

B-CoC-2020.txt
OASIcs-Tokenomics-2019-12.txt
BlockchainBased-2023.txt
ExploringBC-2023.txt


In [14]:
sources = [ doc.metadata['source'] for doc in response['context'] ]
sources

['B-CoC-2020.txt',
 'OASIcs-Tokenomics-2019-12.txt',
 'BlockchainBased-2023.txt',
 'ExploringBC-2023.txt']

## Examples from the documentation

In [14]:
rml_rag_prompt = """HUMAN
You are an assistant for question-answering tasks. Use the following pieces of retrieved context to answer the question. If you don't know the answer, just say that you don't know. Use three sentences maximum and keep the answer concise.
Context: {context} 
Question: {question} 
Answer:
"""
RLM_RAG_PROMPT = ChatPromptTemplate.from_template(rml_rag_prompt)


In [15]:
def format_docs(docs):
    return "\n\n".join(doc.page_content for doc in docs)

rag_chain = (
    {"context": retriever | format_docs, "question": RunnablePassthrough()}
    | RLM_RAG_PROMPT
    | model
    | StrOutputParser()
)

In [16]:
rag_chain.invoke("What is Data Governance?")

'Data governance is the process of managing the availability, usability, integrity, and security of data in enterprise systems, based on internal data standards and policies. It ensures data is consistent, trustworthy, and not misused, and is critical for organizations due to increasing data privacy regulations and reliance on data analytics. A well-designed data governance program includes teams, a steering committee, and data stewards that create and enforce data standards. Effective data governance focuses on expected business benefits.'

Prompt with context

In [17]:
contextualize_q_system_prompt = """Given a chat history and the latest user question \
which might reference context in the chat history, formulate a standalone question \
which can be understood without the chat history. Do NOT answer the question, \
just reformulate it if needed and otherwise return it as is."""

contextualize_q_prompt = ChatPromptTemplate.from_messages(
    [
        ("system", contextualize_q_system_prompt),
        MessagesPlaceholder(variable_name="chat_history"),
        ("human", "{question}"),
    ]
)

contextualize_q_chain = contextualize_q_prompt | model | StrOutputParser()

contextualize_q_chain.invoke(
    {
        "chat_history": [
            HumanMessage(content="What does LLM stand for?"),
            AIMessage(content="Large language model"),
        ],
        "question": "What is meant by large",
    }
)

'In the context of language models, "large" generally refers to a model that has a larger number of parameters, as compared to smaller models. This size typically allows the model to have a better understanding of complex language patterns and a wider range of topics, at the cost of increased computational requirements.'

Chain with chat history

In [18]:
qa_system_prompt = """You are an assistant for question-answering tasks.
Use the following pieces of retrieved context to answer the question.
If you don't know the answer, just say that you don't know.
Use three sentences maximum and keep the answer concise.

{context}"""
qa_prompt = ChatPromptTemplate.from_messages(
    [
        ("system", qa_system_prompt),
        MessagesPlaceholder(variable_name="chat_history"),
        ("human", "{question}"),
    ]
)


def contextualized_question(input: dict):
    if input.get("chat_history"):
        return contextualize_q_chain
    else:
        return input["question"]


rag_chain = (
    RunnablePassthrough.assign(
        context=contextualized_question | retriever | format_docs
    )
    | qa_prompt
    | model
)

In [19]:
chat_history = []

question = "What is a Blockchain?"
ai_msg = rag_chain.invoke({"question": question, "chat_history": chat_history})
chat_history.extend([HumanMessage(content=question), ai_msg])

question = "What are its benefits?"
ai_msg = rag_chain.invoke({"question": question, "chat_history": chat_history})
chat_history.extend([HumanMessage(content=question), ai_msg])


In [20]:
chat_history

[HumanMessage(content='What is a Blockchain?'),
 AIMessage(content='A blockchain is a type of distributed ledger technology that consists of a chain of blocks, where each block contains a list of validated and time-stamped transactions. It is a decentralized system with a consensus mechanism, allowing multiple participants to maintain copies of the ledger, ensuring security, immutability, and transparency of recorded data. Blockchains can be classified as public, private/permissioned, or hybrid, each with different data access levels. The original blockchain technology was employed for the Bitcoin cryptocurrency and uses a consensus process based on Proof-of-Work (PoW).'),
 HumanMessage(content='What are its benefits?'),
 AIMessage(content="Blockchain technology offers several benefits, including:\n\n1. Transparency: Blockchain's public nature allows members and non-members to view and verify transactions, enhancing trust and accountability.\n2. Immutability: Once data is recorded on t

## Working with Runnable

In [21]:
def pipeLog(s:str, x):
    print(s, x)
    return x

pipe_a = RunnableLambda(lambda x: pipeLog("A>",x))
pipe_b = RunnableLambda(lambda x: pipeLog("B>",x))

pipe_a.invoke({'x':"hola"})

A> {'x': 'hola'}


{'x': 'hola'}

In [22]:
rag_chain_with_source = RunnableParallel(
    {"context": itemgetter("question")|retriever, "question": itemgetter("question"), "chat_history": itemgetter("chat_history") }
).assign(answer=rag_chain)


In [23]:
chat_history = []

question = "What is a Blockchain?"
ai_msg = rag_chain_with_source.invoke({"question": question, "chat_history": chat_history})
ai_msg


{'context': [Document(page_content='the nodes present on the chain maintain a complete local copy of the blockchain. The\nblockchain is an indigenous technology that has emerged for decentralized applications\nas the outcome of complication, privacy, and security issues present in the applications\nover half a century [3,4]. It is a peer-to-peer system that authorizes the users to maintain a\nledger for various transactions that are reproduced, and remains identical in more than\none location over multiple user servers [5].\nA blockchain is essentially a block of chains, with the growing list of records referred\nto as blocks that are joined with cryptography [4]. Each blockchain contains a hash of a\nprevious block, and a timestamp that keeps track of the creation and modification time of', metadata={'chunk': 3.0, 'source': 'CustodyBlock-2021.txt'}),
  Document(page_content='customer information [14]. Blockchain is the core strength of IoT so\xad\nlutions to build a system with crypto

In [24]:
rp = RunnableParallel(
    {"input": pipe_a, "context": itemgetter("question")|retriever, "question": itemgetter("question") }
)
rp.invoke({ 'question': "Is this a question?", "chat_history": [] })

A> {'question': 'Is this a question?', 'chat_history': []}


{'input': {'question': 'Is this a question?', 'chat_history': []},
 'context': [Document(page_content='6 | Page', metadata={'chunk': 21.0, 'source': 'Gaia_X_Federation_Services_White_Paper_1_December_2021.txt'}),
  Document(page_content='in the general population of consumers.\nIn conclusion, this is clearly at present merely the beginnings of a modest academic\nproposal with, as can be seen, many details still to be worked out. However, we need to\nstart thinking seriously about alternatives to the current stalemate in the legal debate\nbetween the advocates of principled but impractical European data protection law versus\nthe defenders of ineffective (and likely to stay that way) US privacy protection. We also', metadata={'chunk': 101.0, 'source': 'SSRN_id1857536.txt'}),
  Document(page_content='5 | Page', metadata={'chunk': 17.0, 'source': 'Gaia_X_Federation_Services_White_Paper_1_December_2021.txt'}),
  Document(page_content='Electronic copy available at: https://ssrn.com/abstract

In [25]:
rag_chain_with_source = RunnableParallel(
    {"context": retriever, "question": RunnablePassthrough() }
)
rag_chain_with_source.invoke("hola mundo")

{'context': [Document(page_content='Tipo de activo', metadata={'chunk': 42.0, 'source': 'articles_237907_maestro_mspi.txt'}),
  Document(page_content='personales realizado por él mismo o por su cuenta. En particular, el responsable debe estar obligado a aplicar medidas oportunas\ny eficaces y ha de poder demostrar la conformidad de las actividades de tratamiento con el presente Reglamento, incluida la eficacia\nde las medidas. Dichas medidas deben tener en cuenta la naturaleza, el ámbito, el contexto y los fines del tratamiento, así como\nel riesgo para los derechos y libertades de las personas físicas.”\nPágina: 50 de 160', metadata={'chunk': 129.0, 'source': 'gestion_riesgo_y_evaluacion_impacto_en_tratamientos_datos_personales.txt'}),
  Document(page_content='de conseguir generar más datos, pues actualmente la generación de datos es muy escasa. Frente al\nocéano que tenemos delante, solo estamos viendo el 6%. Además, faltan bases de datos estructuradas\ny con unos datos estandarizado

## Handle Chat History

[BaseChatMessageHistory](https://api.python.langchain.com/en/latest/chat_history/langchain_core.chat_history.BaseChatMessageHistory.html#langchain_core.chat_history.BaseChatMessageHistory)  
[]()  
[]()  
[]()  


In [28]:
# chat_history = []
# memory = ConversationBufferWindowMemory(k=10, input_key='question', output_key='answer')
memory = ConversationBufferMemory(return_messages=True, input_key="question", output_key="answer")

In [29]:
memory.clear()

Chains

In [30]:
qa_system_prompt = """You are an assistant for question-answering tasks.
Use the following pieces of retrieved context to answer the question.
If you don't know the answer, just say that you don't know.
Keep the answer as concise and precise as possible.

{context}"""
qa_prompt = ChatPromptTemplate.from_messages(
    [
        ("system", qa_system_prompt),
        MessagesPlaceholder(variable_name="chat_history"),
        ("human", "{question}"),
    ]
)


def contextualized_question(input: dict):
    if input.get("chat_history"):
        return contextualize_q_chain
    else:
        return input["question"]


rag_chain = (
    RunnablePassthrough.assign(
        context=contextualized_question | retriever | format_docs
    )
    | qa_prompt
    | model
)

rag_chain_with_source = RunnableParallel(
    {"context": itemgetter("question")|retriever, "question": itemgetter("question"), "chat_history": itemgetter("chat_history") }
).assign(answer=rag_chain)


In [31]:
def run_query(question: str):
    ai_msg = rag_chain_with_source.invoke({"question": question, "chat_history": RunnableLambda(memory.load_memory_variables)})
    # chat_history.extend([ HumanMessage(content=question), ai_msg['answer'] ])
    memory.save_context(inputs=question, outputs={"answer": ai_msg["answer"].content})
    print(ai_msg['answer'].content)



In [32]:
run_query("What is a Blockchain?")

ValueError: variable chat_history should be a list of base messages, got {'history': []}

In [93]:
run_query("How is it helpful for data governance?", chat_history)

Blockchain technology can be helpful for data governance by providing a distributed and transparent administration of data. It can enhance trustworthy data sharing by promoting data quality, assessing input data sets, effectively managing access control, and presenting data provenance and activity monitoring. The use of an assessment model that includes reputation, endorsement, and confidence factors can further evaluate data quality. Additionally, blockchain technology can support data use while aligning technology development with personal, ethical, and democratic values. It can also provide an infrastructure for data trust, which is essential for creating economic and social value from data analysis.


In [94]:
chat_history

[HumanMessage(content='What is a Blockchain?'),
 AIMessage(content='A blockchain is a series of linked data structures, called blocks, that store and monitor the status of distributed systems on a peer-to-peer network. Each block contains a hash of a previous block and a timestamp, and is connected to a previous block. It is a decentralized and transparent technology, where multiple participants maintain copies of the ledger, providing secure and immutable record-keeping of digital transactions.'),
 HumanMessage(content='How is it helpful for data governance?'),
 AIMessage(content='Blockchain technology can be helpful for data governance by providing a distributed and transparent administration of data. It can enhance trustworthy data sharing by promoting data quality, assessing input data sets, effectively managing access control, and presenting data provenance and activity monitoring. The use of an assessment model that includes reputation, endorsement, and confidence factors can fur

In [133]:
loaded_memory.invoke({ 'history': ['aaa','bbb'] })

{'history': ['aaa', 'bbb'], 'chat_history': ''}

In [159]:
memory.memory_variables

['history']

## Another implementation Conversation+Memery+RAG

In [35]:
memory.clear()

In [33]:
DEFAULT_DOCUMENT_PROMPT = PromptTemplate.from_template(template="{page_content}")

def _combine_documents(
    docs, document_prompt=DEFAULT_DOCUMENT_PROMPT, document_separator="\n\n"
):
    doc_strings = [format_document(doc, document_prompt) for doc in docs]
    return document_separator.join(doc_strings)

In [36]:
_template = """Given the following conversation and a follow up question, rephrase the follow up question to be a standalone question, in its original language.

Chat History:
{chat_history}
Follow Up Input: {question}
Standalone question:"""
CONDENSE_QUESTION_PROMPT = PromptTemplate.from_template(_template)

template = """Answer the question based only on the following context:
{context}

Question: {question}
"""
ANSWER_PROMPT = ChatPromptTemplate.from_template(template)

In [38]:
loaded_memory = RunnablePassthrough.assign(
    chat_history=RunnableLambda(memory.load_memory_variables) | itemgetter("history"),
)

standalone_question = {
    "standalone_question": {
        "question": lambda x: x["question"],
        "chat_history": lambda x: get_buffer_string(x["chat_history"]),
    }
    | CONDENSE_QUESTION_PROMPT
    | model
    | StrOutputParser()
}

# Now we retrieve the documents
retrieved_documents = {
    "docs": itemgetter("standalone_question") | retriever,
    "question": lambda x: x["standalone_question"],
}

# Now we construct the inputs for the final prompt
final_inputs = {
    "context": lambda x: _combine_documents(x["docs"]),
    "question": itemgetter("question"),
}

# And finally, we do the part that returns the answers
answer = {
    "answer": final_inputs | ANSWER_PROMPT | model,
    "docs": itemgetter("docs"),
}

# And now we put it all together!
final_chain = loaded_memory | standalone_question | retrieved_documents | answer


In [39]:
inputs = { 'question': 'What is a blockchain?' }
result = final_chain.invoke(inputs)
# memory.save_context(inputs={'question':HumanMessage(inputs['question'])}, outputs={'answer': result["answer"]})
memory.save_context(inputs, {"answer": result["answer"].content})
result

{'answer': AIMessage(content='Blockchain is a distributed ledger technology that enables secure and immutable record-keeping of digital transactions. It comprises a chain of blocks, each containing a list of validated and time-stamped transactions. The decentralized nature of blockchain ensures that multiple participants, or nodes, maintain copies of the ledger, making it resistant to tampering and censorship. This allows for a trustworthy environment in the registering of sensitive information, as it can provide an audit trail of all operations carried out between peers without the need for a centralized authority. Public blockchains are characterized by their transparency, allowing members and non-members to view and verify the transactions.'),
 'docs': [Document(page_content='Does this work mention which blockchain platform was used?\nDoes this work use smart contracts as part of the solution?\nDoes this work describe the motivation for using blockchain as a technological solution?\

In [40]:
# memory.memory_variables
inputs['question']

'What is a blockchain?'

In [41]:
memory.load_memory_variables({})

{'history': [HumanMessage(content='What is a blockchain?'),
  AIMessage(content='Blockchain is a distributed ledger technology that enables secure and immutable record-keeping of digital transactions. It comprises a chain of blocks, each containing a list of validated and time-stamped transactions. The decentralized nature of blockchain ensures that multiple participants, or nodes, maintain copies of the ledger, making it resistant to tampering and censorship. This allows for a trustworthy environment in the registering of sensitive information, as it can provide an audit trail of all operations carried out between peers without the need for a centralized authority. Public blockchains are characterized by their transparency, allowing members and non-members to view and verify the transactions.')]}

In [42]:
inputs = { 'question': 'How does it help data governance?' }
result = final_chain.invoke(inputs)
memory.save_context(inputs, {"answer": result["answer"].content})
# memory.save_context(inputs={'question':inputs['question']}, outputs={'answer': result["answer"].content})
result

{'answer': AIMessage(content="Based on the provided context, blockchain technology contributes to data governance in several ways. First, it can provide a decentralized and transparent method for data circulation, allowing for traceability and accountability in data handling. This is achieved through blockchain's ability to maintain a tamper-proof record of data transactions, which can promote data quality by assessing input data sets and presenting data provenance and activity monitoring.\n\nFurthermore, blockchain technology can effectively manage access control in data governance. By utilizing smart contracts, data access and permissions can be automatically enforced and audited, ensuring that only authorized parties can access specific data. This can be particularly useful in multi-stakeholder scenarios, such as genomic data sharing, where transparent and participatory access control is essential.\n\nHowever, it is important to note that the governance design of blockchain systems 

In [43]:
pipe_a = RunnableLambda(lambda x: pipeLog("A>",x))
pipe_b = RunnableLambda(lambda x: pipeLog("B>",x))
pipe_c = RunnableLambda(lambda x: pipeLog("C>",x))

test_chain = pipe_a | loaded_memory | pipe_b | standalone_question | pipe_c
test_chain.invoke({'question' : 'How does it help transparency?'})

A> {'question': 'How does it help transparency?'}
B> {'question': 'How does it help transparency?', 'chat_history': [HumanMessage(content='What is a blockchain?'), AIMessage(content='Blockchain is a distributed ledger technology that enables secure and immutable record-keeping of digital transactions. It comprises a chain of blocks, each containing a list of validated and time-stamped transactions. The decentralized nature of blockchain ensures that multiple participants, or nodes, maintain copies of the ledger, making it resistant to tampering and censorship. This allows for a trustworthy environment in the registering of sensitive information, as it can provide an audit trail of all operations carried out between peers without the need for a centralized authority. Public blockchains are characterized by their transparency, allowing members and non-members to view and verify the transactions.'), HumanMessage(content='How does it help data governance?'), AIMessage(content="Based on the

{'standalone_question': 'How does blockchain technology help with transparency?'}

In [44]:
inputs = { 'question': 'What purpose may the consensus mechanism serve?' }
result = final_chain.invoke(inputs)
memory.save_context(inputs, {"answer": result["answer"].content})
result['answer'].content

'The consensus mechanism in blockchain technology is responsible for the orderly creation of a unique sequence of transactions in a blockchain network. It enables the network to agree on the validity and arrangement of transactions in a decentralized manner. The consensus algorithm orders transactions into blocks, and once a block is consensusly accepted and added to the blockchain, it becomes immutable and unalterable. This ensures the security, transparency, and integrity of the recorded data in the ledger.'

In [45]:
inputs = { 'question': 'Can it help with data governance?' }
result = final_chain.invoke(inputs)
memory.save_context(inputs, {"answer": result["answer"].content})
result['answer'].content

"Consensus mechanisms in blockchain technology can contribute to data governance by providing a distributed and transparent administration that ensures data quality, manages access control, and monitors data provenance. The consensus mechanism in blockchain technology enables multiple parties to maintain consensus on an immutable ledger, which can be used to assess input data sets, promote data quality, and handle a large number of transactions with low latency. Additionally, consensus mechanisms can be used to establish an adaptive solution for determining the number of transaction validators based on the computed trust value. This can help ensure the trustworthiness and quality of the data at origin and ethical and secure usage of the data at the end, addressing both data owners' and data users' concerns. However, consensus mechanisms in blockchain technology still require governance structures to establish compliance with data protection and other laws and to establish liability."